In [1]:
import pandas as pd
import numpy as np
from src import Utils, LSTM
from skorch.dataset import ValidSplit
from torch.nn import BCEWithLogitsLoss, NLLLoss, BCELoss

/tmp/ipykernel_32217/1386655886.py:1: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd
/home/nate/miniconda3/lib/python3.9/site-packages/spacy/util.py:918: UserWarning: [W094] Model 'tl_calamancy_md' (0.1.0) specifies an under-constrained spaCy version requirement: >=3.5.0. This can lead to compatibility problems with older versions, or as new spaCy versions are released, because the model may say it's compatible when it's not. Consider changing the "spacy_version" in your meta.json to a version range, with a lower and upper pin. For example: >=3.7.4,<3.8.0
  warnings.warn(warn_msg)
/home/nate/minicon

In [2]:
MODEL_FOLDER = 'model_lstm'

In [3]:
dataset = Utils.read_csv_file('datasets/datasetall.csv')
dataset

CSV file read successfully!


text  label
0      Binay: Patuloy ang kahirapan dahil sa maling p...      0
1      SA GOBYERNONG TAPAT WELCOME SA BAGUO ANG LAHAT...      0
2      wait so ur telling me Let Leni Lead mo pero NY...      1
3       [USERNAME]wish this is just a nightmare that ...      0
4                   doc willie ong and isko sabunutan po      0
...                                                  ...    ...
28456    Bisaya, Probinsyano/a, mostly Bisaya = katulong      1
28457  Amnesia. In my whole life wala pa ako nakasala...      1
28458  Kontrabida na ilang beses na tinalo at obvious...      1
28459  Yung antagonist laging kailangang sobrang sama...      1
28460  May nabaril or nasaksak na pero 'di pa tatawag...      1

[28461 rows x 2 columns]

In [4]:
Utils.seed_random_number_generators()

Random number generators seeded.


In [5]:
TEST_SIZE = 0.1

X_train, X_test, y_train, y_test = Utils.get_train_test_split(dataset, TEST_SIZE)

In [6]:
X_train

0        pag hindi nanalo si Norberto Gonzales pwede ba...
1        Ngayon lang ako super proud sa PRESIDENTE na i...
2        JUST SAW SOMEONE CALL BBM BLENGBLONG HAHAHAHAH...
3        Rep. Binay on her leadership style: I am very ...
4        Liwanag o dilim? May oras pa. Kakampink Leni L...
                               ...                        
25611    "Kala ko wala andito pala si Marcos."*pertaini...
25612    cathy [USERNAME] Dec [USERNAME] parang tanga i...
25613                             Nognog+pandak= BINAY ftw
25614    BINAY:Did your enormous wealth all come from y...
25615                                Uunlad tayo kay Binay
Name: text, Length: 25616, dtype: object

In [7]:
y_train

0        1
1        0
2        1
3        0
4        0
        ..
25611    0
25612    1
25613    1
25614    1
25615    0
Name: label, Length: 25616, dtype: int64

In [8]:
X_test

0       PRESIDENTE DUTERTE I'm sure in last debateitao...
1       CHANGE IS BADLY NEEDED No To Mar Roxas2016 Dut...
2                                One Pink March Leni Kiko
3                               see youuu later Leni Kiko
4       [USERNAME] Nangyari na yan eh pero kahit anong...
                              ...                        
2840    kaya siguro umabot ng milyon yung boto kay MAR...
2841    Dedicating my 21km run for my chosen Presand V...
2842    Bakit si Mar? Because DuterteGrace Poe and VP ...
2843    patalo po ung patalastas ni Mar Roxas....malas...
2844    Kapihan with Sen. Bongbong Marcos startshe say...
Name: text, Length: 2845, dtype: object

In [9]:
y_test

0       0
1       0
2       0
3       0
4       0
       ..
2840    1
2841    0
2842    1
2843    1
2844    0
Name: label, Length: 2845, dtype: int64

In [10]:
epochs = [100, 200, 300]
learning_rate = [0.1, 0.01, 0.001, 0.0001, 0.00001]
batch_size = [32, 64, 128]
hidden_size = [100, 200, 300, 400]
num_layers = [1, 2, 3]

train_lstm = LSTM.LstmPipeline

In [11]:
train_lstm.set_params(
  lstm__train_split=None,
  # lstm__module__input_size=300,
  lstm__module__hidden_size=250,
  lstm__module__num_layers=1,
  lstm__module__output_size=1,
  lstm__optimizer__lr=0.015,
  lstm__max_epochs=30,
  lstm__batch_size=32,
  tokenizer__remove_stopwords=False,
  lstm__criterion=BCEWithLogitsLoss,
)

train_lstm['lstm'].callbacks[0].dirname = f'{MODEL_FOLDER}/train_lstm'
train_lstm['lstm'].callbacks[0].monitor = 'train_loss_best'

In [12]:
train_lstm

Pipeline(steps=[('tokenizer', CalamancyTokenizer()),
                ('lstm',
                 <class 'skorch.classifier.NeuralNetClassifier'>[uninitialized](
  module=<class 'src.LSTM.LstmModel'>,
  module__hidden_size=250,
  module__num_layers=1,
  module__output_size=1,
))])

In [13]:
train_lstm.fit(X_train, y_train.astype(np.float32))

  0%|          | 0/801 [00:00<?, ?it/s]

tensor([1., 0., 1., 0., 0., 1., 1., 1., 0., 1., 1., 1., 1., 0., 0., 1., 1., 0.,
        0., 1., 1., 1., 0., 0., 0., 1., 0., 1., 1., 0., 1., 1.],
       device='cuda:0')
tensor([0., 1., 0., 0., 1., 1., 1., 1., 1., 1., 1., 1., 1., 0., 1., 0., 0., 1.,
        1., 0., 0., 1., 1., 1., 0., 0., 0., 1., 0., 1., 0., 1.],
       device='cuda:0')
tensor([1., 1., 0., 0., 0., 1., 1., 1., 1., 0., 1., 0., 1., 1., 1., 0., 1., 1.,
        1., 0., 0., 0., 1., 0., 1., 1., 0., 1., 1., 0., 1., 1.],
       device='cuda:0')
tensor([0., 0., 1., 0., 0., 0., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 0., 1., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0.],
       device='cuda:0')
tensor([0., 0., 0., 0., 1., 1., 0., 0., 0., 0., 0., 1., 1., 1., 1., 0., 1., 1.,
        0., 1., 0., 1., 1., 0., 1., 1., 1., 1., 1., 0., 0., 1.],
       device='cuda:0')
tensor([0., 1., 1., 1., 0., 1., 0., 0., 0., 0., 0., 1., 0., 0., 1., 1., 1., 0.,
        0., 0., 1., 1., 1., 0., 1., 0., 0., 0., 1., 1., 1., 1.],
       dev

  0%|          | 0/801 [00:00<?, ?it/s]

tensor([1., 0., 1., 0., 0., 1., 1., 1., 0., 1., 1., 1., 1., 0., 0., 1., 1., 0.,
        0., 1., 1., 1., 0., 0., 0., 1., 0., 1., 1., 0., 1., 1.],
       device='cuda:0')
tensor([0., 1., 0., 0., 1., 1., 1., 1., 1., 1., 1., 1., 1., 0., 1., 0., 0., 1.,
        1., 0., 0., 1., 1., 1., 0., 0., 0., 1., 0., 1., 0., 1.],
       device='cuda:0')
tensor([1., 1., 0., 0., 0., 1., 1., 1., 1., 0., 1., 0., 1., 1., 1., 0., 1., 1.,
        1., 0., 0., 0., 1., 0., 1., 1., 0., 1., 1., 0., 1., 1.],
       device='cuda:0')
tensor([0., 0., 1., 0., 0., 0., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 0., 1., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0.],
       device='cuda:0')
tensor([0., 0., 0., 0., 1., 1., 0., 0., 0., 0., 0., 1., 1., 1., 1., 0., 1., 1.,
        0., 1., 0., 1., 1., 0., 1., 1., 1., 1., 1., 0., 0., 1.],
       device='cuda:0')
tensor([0., 1., 1., 1., 0., 1., 0., 0., 0., 0., 0., 1., 0., 0., 1., 1., 1., 0.,
        0., 0., 1., 1., 1., 0., 1., 0., 0., 0., 1., 1., 1., 1.],
       dev

  0%|          | 0/801 [00:00<?, ?it/s]

...

  0%|          | 0/801 [00:00<?, ?it/s]

tensor([1., 0., 1., 0., 0., 1., 1., 1., 0., 1., 1., 1., 1., 0., 0., 1., 1., 0.,
        0., 1., 1., 1., 0., 0., 0., 1., 0., 1., 1., 0., 1., 1.],
       device='cuda:0')
tensor([0., 1., 0., 0., 1., 1., 1., 1., 1., 1., 1., 1., 1., 0., 1., 0., 0., 1.,
        1., 0., 0., 1., 1., 1., 0., 0., 0., 1., 0., 1., 0., 1.],
       device='cuda:0')
tensor([1., 1., 0., 0., 0., 1., 1., 1., 1., 0., 1., 0., 1., 1., 1., 0., 1., 1.,
        1., 0., 0., 0., 1., 0., 1., 1., 0., 1., 1., 0., 1., 1.],
       device='cuda:0')
tensor([0., 0., 1., 0., 0., 0., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 0., 1., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0.],
       device='cuda:0')
tensor([0., 0., 0., 0., 1., 1., 0., 0., 0., 0., 0., 1., 1., 1., 1., 0., 1., 1.,
        0., 1., 0., 1., 1., 0., 1., 1., 1., 1., 1., 0., 0., 1.],
       device='cuda:0')
tensor([0., 1., 1., 1., 0., 1., 0., 0., 0., 0., 0., 1., 0., 0., 1., 1., 1., 0.,
        0., 0., 1., 1., 1., 0., 1., 0., 0., 0., 1., 1., 1., 1.],
       dev

  0%|          | 0/801 [00:00<?, ?it/s]

tensor([1., 0., 1., 0., 0., 1., 1., 1., 0., 1., 1., 1., 1., 0., 0., 1., 1., 0.,
        0., 1., 1., 1., 0., 0., 0., 1., 0., 1., 1., 0., 1., 1.],
       device='cuda:0')
tensor([0., 1., 0., 0., 1., 1., 1., 1., 1., 1., 1., 1., 1., 0., 1., 0., 0., 1.,
        1., 0., 0., 1., 1., 1., 0., 0., 0., 1., 0., 1., 0., 1.],
       device='cuda:0')
tensor([1., 1., 0., 0., 0., 1., 1., 1., 1., 0., 1., 0., 1., 1., 1., 0., 1., 1.,
        1., 0., 0., 0., 1., 0., 1., 1., 0., 1., 1., 0., 1., 1.],
       device='cuda:0')
tensor([0., 0., 1., 0., 0., 0., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 0., 1., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0.],
       device='cuda:0')
tensor([0., 0., 0., 0., 1., 1., 0., 0., 0., 0., 0., 1., 1., 1., 1., 0., 1., 1.,
        0., 1., 0., 1., 1., 0., 1., 1., 1., 1., 1., 0., 0., 1.],
       device='cuda:0')
tensor([0., 1., 1., 1., 0., 1., 0., 0., 0., 0., 0., 1., 0., 0., 1., 1., 1., 0.,
        0., 0., 1., 1., 1., 0., 1., 0., 0., 0., 1., 1., 1., 1.],
       dev

Pipeline(steps=[('tokenizer', CalamancyTokenizer()),
                ('lstm',
                 <class 'skorch.classifier.NeuralNetClassifier'>[initialized](
  module_=LstmModel(
    (lstm): LSTM(200, 250, batch_first=True)
    (fc): Linear(in_features=250, out_features=1, bias=True)
  ),
))])

In [14]:
accuracy, recall, precision, f1 = Utils.get_prediction_results(
  X_test,
  y_test,
  train_lstm,
)

Accuracy: 0.7894551845342707
Recall: 0.8619246861924686
Precision: 0.7550397067806964
F1-score: 0.8049495278410942


In [15]:
Utils.save_trained_model(train_lstm, f"{MODEL_FOLDER}/LSTM")

Ensemble model saved to Pipeline(steps=[('tokenizer', CalamancyTokenizer()),
                ('lstm',
                 <class 'skorch.classifier.NeuralNetClassifier'>[initialized](
  module_=LstmModel(
    (lstm): LSTM(200, 250, batch_first=True)
    (fc): Linear(in_features=250, out_features=1, bias=True)
  ),
))]).pkl


In [16]:
history_data_frame = pd.DataFrame(
    train_lstm['lstm'].history
).set_index('epoch')
history_data_frame.to_csv(f'{MODEL_FOLDER}/lstm_history.csv')

In [17]:
history_data_frame

batches  train_batch_count  \
epoch                                                                         
1      [{'train_loss': 0.6880549192428589, 'train_bat...                801   
2      [{'train_loss': 0.3945254683494568, 'train_bat...                801   
3      [{'train_loss': 0.449358195066452, 'train_batc...                801   
4      [{'train_loss': 0.46639764308929443, 'train_ba...                801   
5      [{'train_loss': 0.4695538580417633, 'train_bat...                801   
6      [{'train_loss': 0.4773753881454468, 'train_bat...                801   
7      [{'train_loss': 0.44208478927612305, 'train_ba...                801   
8      [{'train_loss': 0.46421945095062256, 'train_ba...                801   
9      [{'train_loss': 0.47764021158218384, 'train_ba...                801   
10     [{'train_loss': 0.46809205412864685, 'train_ba...                801   
11     [{'train_loss': 0.4985300302505493, 'train_bat...                801   
12     [{'train_loss': 0.430505633354187, 'train_batc...                801   
13     [{'train_loss': 0.4538881182670593, 'train_bat...                801   
14     [{'train_loss': 0.4765767455101013, 'train_bat...                801   
15     [{'train_loss': 0.44346362352371216, 'train_ba...                801   
16     [{'train_loss': 0.3839547038078308, 'train_bat...                801   
17     [{'train_loss': 0.42955654859542847, 'train_ba...                801   
18     [{'train_loss': 0.3902125060558319, 'train_bat...                801   
19     [{'train_loss': 0.4141077399253845, 'train_bat...                801   
20     [{'train_loss': 0.43565505743026733, 'train_ba...                801   
21     [{'train_loss': 0.4547785818576813, 'train_bat...                801   
22     [{'train_loss': 0.39706194400787354, 'train_ba...                801   
23     [{'train_loss': 0.449221134185791, 'train_batc...                801   
24     [{'train_loss': 0.4313622713088989, 'train_bat...                801   
25     [{'train_loss': 0.4393375515937805, 'train_bat...                801   

            dur  train_loss  train_loss_best  event_cp  
epoch                                                   
1      6.881619    0.475329             True      True  
2      6.387395    0.444791             True      True  
3      6.265682    0.433975             True      True  
4      6.933944    0.422526             True      True  
5      7.795602    0.414166             True      True  
6      7.361485    0.409515             True      True  
7      7.451346    0.405288             True      True  
8      7.804704    0.425639            False     False  
9      7.982363    0.409423            False     False  
10     9.993481    0.407038            False     False  
11     8.475361    0.398138             True      True  
12     7.581991    0.393850             True      True  
13     7.277092    0.396304            False     False  
14     7.595903    0.404072            False     False  
15     7.660583    0.396530            False     False  
16     7.946487    0.388392             True      True  
17     7.582116    0.388457            False     False  
18     7.765574    0.385056             True      True  
19     7.208577    0.384030             True      True  
20     7.565136    0.381980             True      True  
21     7.561774    0.383567            False     False  
22     7.464933    0.380565             True      True  
23     7.545385    0.380941            False     False  
24     7.399558    0.380266             True      True  
25     7.618831    0.378982             True      True

In [18]:
metrics_data_frame = pd.DataFrame([{
  'accuracy': accuracy,
  'recall': recall,
  'precision': precision,
  'f1': f1,
}])
metrics_data_frame.to_csv(f'{MODEL_FOLDER}/lstm_metrics.csv')